This notebook generates dataset according to CrossDock 100k subset
- The goal is to use full protein from original CrossDock dataset instead of the version with 12A cutoff.
- pockets not from PDBBind set are removed 

You need to have CrossDock subset and full set downloaded to run this script.

In [2]:
import os
from glob import glob
import torch
from tqdm import tqdm
from collections import defaultdict 
import sys

sys.path.append('../')

from src.tacogfn.eval import docking
from src.tacogfn.utils import molecules

/home/tsa87/anaconda3/envs/tacogfn/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


There are 24478 receptors

In [13]:
pocket_paths = glob('../dataset/crossdock/*_rec.pdb')
len(pocket_paths)

44646

There are 21231 ligands

In [14]:
ligand_paths = glob('../dataset/crossdock/*_lig.pdb')
len(ligand_paths)

22288

In [58]:
pocket_ids = [i.split('/')[-1].split('_rec')[0] for i in pocket_paths]

In [59]:
pocket_ids_to_paths = dict(zip(pocket_ids, pocket_paths))

We now match ligands to pockets based on filenames and resolve based on docking scores

In [24]:
# Pocket2Mol pdb ids
split_by_name = torch.load('../dataset/split_by_name.pt')
train_pdb_ids = [val[0].split('/')[-1].split('_rec')[0] for val in split_by_name['train']]
val_pdb_ids = [val[0].split('/')[-1].split('_rec')[0] for val in split_by_name['test']]
pocket2mol_split = split_by_name['train'] + split_by_name['test']
pocket2mol_pdb_ids = set(train_pdb_ids + val_pdb_ids)

In [35]:
cross_dock_pocket_ids = set(pocket_ids)

In [66]:
pocket_to_ligands = {}

for pair in pocket2mol_split:
    pdb_id = pair[0].split('/')[-1].split('_rec')[0]
    ligand_path = pair[1]

    pocket_to_ligands[pdb_id] = ligand_path

In [67]:
torch.save(pocket_to_ligands, '../dataset/pocket_to_ligands.pt')

Compute pocket centroids

In [7]:
pocket_to_ligands = torch.load('../dataset/pocket_to_ligands.pt')

In [23]:
pocket_to_centroid = {}
for key, lig_path in pocket_to_ligands.items():
    lig_path = os.path.join('../dataset/crossdocked_pocket10/', lig_path)
    pocket_to_centroid[key] = molecules.get_centroid_from_sdf(lig_path)

In [25]:
torch.save(pocket_to_centroid, '../dataset/pocket_to_centroid.pt')

Compute pocket to native ligand docking scores

In [4]:
pocket_to_ligands = torch.load('../dataset/pocket_to_ligands.pt')

In [10]:
from src.tacogfn.eval import docking

for key, lig_path in tqdm(pocket_to_ligands.items()):
    rec_path = os.path.join('../dataset/crossdock/', key + '_rec.pdb')
    target_path = rec_path.replace('.pdb', '.pdbqt').replace('crossdock', 'crossdock_pdbqt')
    if not os.path.exists(target_path):
        docking._prepare_receptor(
            rec_path,
            target_path
        )

  0%|          | 1/15307 [00:00<1:11:56,  3.55it/s]

WARNING! 4xe6_X_rec has 7  atoms with alternate locations named ['A']!

WARNING! using alternate location A
adding gasteiger charges to peptide
Sorry, there are no Gasteiger parameters available for atom 1k1j_A_rec:A:CA 480:CA


  0%|          | 2/15307 [00:00<1:22:24,  3.10it/s]

WARNING! 5ai4_A_rec has 22  atoms with alternate locations named ['A']!

WARNING! using alternate location A
adding gasteiger charges to peptide


  0%|          | 3/15307 [00:01<2:40:36,  1.59it/s]

...

WARNING! 1ykl_B_rec has 72  atoms with alternate locations named ['A']!

WARNING! using alternate location A
adding gasteiger charges to peptide
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:A:LYS154:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:A:LYS154:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:B:LYS507:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:B:LYS507:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:C:LYS154:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:C:LYS154:NZ
Unable to assign MAP type to atom N
Sorry, there are no Gasteiger parameters available for atom 1ykl_B_rec:D:LYS507:NZ
Unable to assign MAP t

 87%|████████▋ | 13271/15307 [3:55:38<2:58:04,  5.25s/it]

adding gasteiger charges to peptide


 87%|████████▋ | 13272/15307 [3:55:39<2:11:19,  3.87s/it]

WARNING! 2qe0_B_rec has 24  atoms with alternate locations named ['A']!

WARNING! using alternate location A
adding gasteiger charges to peptide


In [ ]:
pocket_to_score = {}
for key, lig_path in tqdm(pocket_to_ligands.items()):
    rec_path = os.path.join('../dataset/crossdock_pdbqt/', key + '_rec.pdbqt')
    lig_path = os.path.join('../dataset/crossdocked_pocket10/', lig_path)
    
    score = docking.compute_docking_score_from_sdf(
        pdb_path=rec_path,
        sdf_path=lig_path,
        local_search=True,
    )
    
    pocket_to_score[key] = score

  0%|          | 0/15307 [00:00<?, ?it/s]

WARNING! 4xe6_X_rec has 7  atoms with alternate locations named ['A']!

WARNING! using alternate location A
adding gasteiger charges to peptide


  0%|          | 1/15307 [00:00<2:59:48,  1.42it/s]

Sorry, there are no Gasteiger parameters available for atom 1k1j_A_rec:A:CA 480:CA


  0%|          | 2/15307 [00:01<3:11:17,  1.33it/s]

...

adding gasteiger charges to peptide


  0%|          | 13/15307 [00:16<4:52:36,  1.15s/it]

WARNING! 5pnx_A_rec has 39  atoms with alternate locations named ['A']!

WARNING! using alternate location A
Sorry, there are no Gasteiger parameters available for atom 5pnx_A_rec:A:NA 204:NA


  0%|          | 13/15307 [00:16<5:31:31,  1.30s/it]


KeyboardInterrupt: 

In [ ]:
torch.save(pocket_to_score, '../dataset/pocket_to_score.pt')